In [1]:
import requests
from bs4 import BeautifulSoup
import re
from datetime import datetime


In [2]:
cookie = 'Bifrost_SessionID=zgu1od3zdklehztwai052g51'

In [3]:
doc_id = 12996221

In [4]:
def part_text(part,start,end):
    part_list = []
    for i in part[start:end]:
        part_list.append(i.get_text().replace('\r', '').replace('\n', '').strip())
        part_text = '\n'.join(part_list)
    return part_text
        

In [5]:
def get_id_details(cookie,doc_id):
    # URL cần gửi yêu cầu
    url = f"https://ecosys.gov.vn/CertificatesUpgrade/Business/CertificateDisplay.aspx?DocId={doc_id}"

    # Headers cần thiết
    headers = {
        "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7",
        "Accept-Language": "en-US,en;q=0.9,vi;q=0.8,vi-VN;q=0.7",
        "Cache-Control": "max-age=0",
        "Connection": "keep-alive",
        "Cookie": cookie,
        "DNT": "1",
        "Referer": "https://ecosys.gov.vn/CertificatesUpgrade/Business/CertificateAdvanceSearch.aspx",
        "Sec-Fetch-Dest": "document",
        "Sec-Fetch-Mode": "navigate",
        "Sec-Fetch-Site": "same-origin",
        "Sec-Fetch-User": "?1",
        "Upgrade-Insecure-Requests": "1",
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/131.0.0.0 Safari/537.36",
        "sec-ch-ua": '"Google Chrome";v="131", "Chromium";v="131", "Not_A Brand";v="24"',
        "sec-ch-ua-mobile": "?0",
        "sec-ch-ua-platform": '"Windows"',
    }

    # Gửi yêu cầu GET
    response = requests.get(url, headers=headers)

    # Kiểm tra phản hồi
    if response.status_code == 200:
        print("Request thành công!")
        # print(response.text)  # In nội dung HTML của trang
    else:
        print(f"Lỗi: {response.status_code}")
        # print(response.text)

    id_info = {}
    id_info["doc_id"] = doc_id
    if response.text:
        soup = BeautifulSoup(response.text,"html.parser")

    info_soup = soup.find('div',id = "ctl00_cplhContainer_rpvInfo") 
    all_div = info_soup.find_all('div', class_=re.compile(r"^row"))
    trang_thai_soup = all_div[0]
    try :
        tths = part_text(trang_thai_soup.find_all('span'),1,3)
        id_info["Trạng thái hồ sơ"] = tths
    except:
        print("not found Trạng thái hồ sơ")
    thong_tin_chung_soup = all_div[1]
    try:
        tax_code = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblCompanyTaxCode").get_text().strip()
        id_info["Tax code"] = tax_code
    except:
        print("Not found tax_code")
    try:
        issuing_authority  = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblDepartment").get_text().strip()
        id_info["Issuing Authority"] = issuing_authority
    except:
        print("Not found Issuing Authority")
    try:
        form  = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblFormCO").get_text().strip()
        id_info["Form"] = form
    except:
        print("Not found form")
    try:
        ImportingCountry   = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblMarket").get_text().strip()
        id_info["Importing_Country"] = ImportingCountry
    except:
        print("Not found Importing Country")
    try:
        Reference_no    = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblCertificateNumber").get_text().strip()
        id_info["Reference No."] = Reference_no
    except:
        print("Not found Reference No.")
    try:
        Issuance_date = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblCertificateDate").get_text().strip()
        id_info["Issuance date"] = Issuance_date
    except:
        print("Not found Issuance date ")
    try:
        Certified_date  = thong_tin_chung_soup.find("span", id = "ctl00_cplhContainer_lblReviewDateApprove").get_text().strip()
        id_info["Certified date"] = Certified_date
    except:
        print("Not found Certified date ")
    try:
        invoiceItems  = thong_tin_chung_soup.find('div',  id = "ctl00_cplhContainer_pnlCustomsNumber").find_all('div',class_ = "invoiceItem")
    except:
        invoiceItems = []
    ExportDeclaration = []
    item_num = 0
    for item in invoiceItems:
        invoiceitem_info = {}
        item_num += 1
        invoiceitem_info["item_num"] = item_num
        
        try: 
            invoice_number = item.find("span", id=lambda x: x and x.startswith("ctl00_cplhContainer_pnlCustomsNumber") and "lblInvoiceNumber" in x)
            invoiceitem_info['invoice_number'] = invoice_number.get_text() 
        except:
            invoiceitem_info['invoice_number'] = ""
            
        try:    
            invoice_date = item.find("span", id=lambda x: x and x.startswith("ctl00_cplhContainer_pnlCustomsNumber") and x.endswith("lblInvoiceDate"))
            invoiceitem_info['invoice_date'] = invoice_date.get_text() 
        except:
            invoiceitem_info['invoice_date'] = ""
            
        try: 
            invoice_link = item.find("a", id=lambda x: x and x.startswith("ctl00_cplhContainer_pnlCustomsNumber") and "hplInvoiceLink" in x)
            invoiceitem_info['invoice_link'] = invoice_link.get("href")
        except:
            invoiceitem_info['invoice_link'] = ""
            
        ExportDeclaration.append(invoiceitem_info)

    id_info["ExportDeclaration"] = ExportDeclaration
    from_to_soup = all_div[2]
    titles = from_to_soup.find_all('span', class_='titles')
    for title in titles:
        key = title.get_text(strip=True)
        div_content = title.find_parent('div').find_next_sibling('div')
        values = [span.get_text(strip=True) for span in div_content.find_all('span')]
        id_info[key] = values

    transport_info_soup = all_div[3]
    try:
        transport_type  = transport_info_soup.find("span", id = "ctl00_cplhContainer_lblTransportMethod").get_text().strip()
        id_info["transport_type"] = transport_type
    except:
        print("Not found transport_type")
    try:
        departure_date  = transport_info_soup.find("span", id = "ctl00_cplhContainer_lblTransportDate").get_text().strip()
        id_info["Departure Date"] = departure_date
    except:
        print("Not found Departure Date")
    try:
        vessel_aircraft_name  = transport_info_soup.find("span", id = "ctl00_cplhContainer_lblShipName").get_text().strip()
        id_info["vessel_aircraft_name"] = vessel_aircraft_name
    except:
        print("Not found Vessel’s Name/Aircraft")
    try:
        port_of_loading  = transport_info_soup.find("span", id = "ctl00_cplhContainer_lblSenderPlace").get_text().strip()
        id_info["port_of_loading"] = port_of_loading
    except:
        print("Not found port_of_loading")
    try:
        port_of_discharge  = transport_info_soup.find("span", id = "ctl00_cplhContainer_lblReceiverPlace").get_text().strip()
        id_info["port_of_discharge"] = port_of_discharge
    except:
        print("Not found port_of_discharge")
    try:
        transport_doc  = transport_info_soup.find("a", id = "ctl00_cplhContainer_hplTransportFileLink").get("href")
        id_info["transport_doc"] = transport_doc
    except:
        print("Not found transport_doc")
    try:
        goods_info_soup = all_div[4].find('table',class_ = 'rgMasterTable')
        # Lấy tiêu đề
        goods_info_header = [th.get_text(separator=" ", strip=True) for th in goods_info_soup.find('thead').find_all('th', class_ = "rgHeader")]

        # Lấy dữ liệu từng dòng trong bảng
        goods_info_rows = []
        for tr in goods_info_soup.find('tbody').find_all('tr'):
            row = [td.get_text(separator=" ", strip=True) for td in tr.find_all('td')]
            goods_info_rows.append(row)
    except:
        print("Not found goods_info")
    goods_info = [goods_info_header] + goods_info_rows
    id_info["goods_info"] = goods_info
    invoice_info_soup = all_div[5]
    try:
        total_value  = invoice_info_soup.find("span", id = "ctl00_cplhContainer_lblTotalItemFobValueTabCO").get_text().strip()
        id_info["total_value"] = total_value
    except:
        print("Not found total_value")
    try:
        total_quantity  = invoice_info_soup.find("span", id = "ctl00_cplhContainer_lblTotalItemQuantityTabCO").get_text().strip()
        id_info["total_quantity"] = total_quantity
    except:
        print("Not found total_quantity")
    try:
        total_weight  = invoice_info_soup.find("span", id = "ctl00_cplhContainer_lblTotalItemGrossWeightTabCO").get_text().strip()
        id_info["total_weight"] = total_weight
    except:
        print("Not found total_weight")
    try:
        show_invoi_checkbox = invoice_info_soup.find("input",  id = "ctl00_cplhContainer_ckbShowOnCO")
        checked = show_invoi_checkbox.has_attr("checked")
        id_info["is_show_fob_value"] = checked
    except:
        print("Not found show_invoi_checkbox")
    try:
        origindoc_soup = invoice_info_soup.find("div",id = "ctl00_cplhContainer_pnlFileCoriginalContent").find_all("a")
        origindoc = [a.get("href") for a in origindoc_soup]
        id_info["origindoc"] = origindoc
    except:
        print("Not found origindoc")
    try:
        invoice_attached_soup = invoice_info_soup.find("div",id = "ctl00_cplhContainer_pnlInvoice").find_all("a")
        invoice_attached = [a.get("href") for a in invoice_attached_soup]
        id_info["invoice_attached"] = invoice_attached
    except:
        print("Not found invoice_attached")
    other_info_soup = all_div[6]
    try:
        declaration_place = other_info_soup.find("span",id = "ctl00_cplhContainer_lblCountryCode").get_text().strip()
        id_info["declaration_place"] = declaration_place
    except:
        print("Not found declaration_place")
    try: 
        spans = other_info_soup.find('table', id = "ctl00_cplhContainer_pnlCertificateOptions_radGridOptions_ctl00").find_all("span",class_ = "chkOption")
        remarks_info = []

        for span in spans:
            label = span.find("label").text.strip()  # Lấy nội dung của thẻ label
            input_tag = span.find("input")          # Lấy thẻ input bên trong
            checked = input_tag.has_attr("checked") # Kiểm tra trạng thái 'checked'
            remarks_info.append({"label": label, "checked": checked})
        id_info["remarks_info"] = remarks_info
    except:
        print("Not found remarks_info")
    print(id_info)
    return id_info

In [6]:
with open("output_ids.txt", "r", encoding="utf-8") as file:
    data_list = [line.strip() for line in file]  # Loại bỏ khoảng trắng và ký tự xuống dòng
all_id_info = []

In [7]:
len(data_list)

903

In [8]:

# Chạy vòng lặp for
for item in data_list:
    id_info = get_id_details(cookie,item)
    all_id_info.append(id_info)

Request thành công!
Not found transport_doc
{'doc_id': '13492295', 'Trạng thái hồ sơ': 'C/O đã được cấp phép\n(ĐÃ NỘP PHÍ)', 'Tax code': '2300956022', 'Issuing Authority': 'Phòng Quản lý XNK khu vực Hà Nội', 'Form': 'Form D', 'Importing_Country': 'Vietnam', 'Reference No.': 'VN-VN 24/01/063026', 'Issuance date': '16/12/2024', 'Certified date': '17/12/2024', 'ExportDeclaration': [{'item_num': 1, 'invoice_number': '306980282400', 'invoice_date': '11/12/2024', 'invoice_link': 'https://ecosys.gov.vn/Resources17/2300956022/2024/12/16/20241216165649_tkx-306980282400.pdf'}], 'Goods consigned from': ['seojin auto company limited', 'plot j5, dai dong-hoan son industrial zone, TAN HONG WARD,', 'TU SON CITY, BACNINH PROVINCE, VIET NAM'], 'Goods consigned to': ['KOREA ELECTRIC TERMINAL VIETNAM CO., LTD', 'LOT CN5, DIEM THUY INDUSTRIAL, DIEM THUY WARD, PHU BINH DISTRICT,', 'THAI NGUYEN PROVINCE, VIET NAM'], 'transport_type': 'By Truck', 'Departure Date': '11/12/2024', 'vessel_aircraft_name': 'BY TR

In [13]:
all_id_info

[{'doc_id': '13492295',
  'Trạng thái hồ sơ': 'C/O đã được cấp phép\n(ĐÃ NỘP PHÍ)',
  'Tax code': '2300956022',
  'Issuing Authority': 'Phòng Quản lý XNK khu vực Hà Nội',
  'Form': 'Form D',
  'Importing_Country': 'Vietnam',
  'Reference No.': 'VN-VN 24/01/063026',
  'Issuance date': '16/12/2024',
  'Certified date': '17/12/2024',
  'ExportDeclaration': [{'item_num': 1,
    'invoice_number': '306980282400',
    'invoice_date': '11/12/2024',
    'invoice_link': 'https://ecosys.gov.vn/Resources17/2300956022/2024/12/16/20241216165649_tkx-306980282400.pdf'}],
  'Goods consigned from': ['seojin auto company limited',
   'plot j5, dai dong-hoan son industrial zone, TAN HONG WARD,',
   'TU SON CITY, BACNINH PROVINCE, VIET NAM'],
  'Goods consigned to': ['KOREA ELECTRIC TERMINAL VIETNAM CO., LTD',
   'LOT CN5, DIEM THUY INDUSTRIAL, DIEM THUY WARD, PHU BINH DISTRICT,',
   'THAI NGUYEN PROVINCE, VIET NAM'],
  'transport_type': 'By Truck',
  'Departure Date': '11/12/2024',
  'vessel_aircraft_name

In [14]:
import pyodbc

# Kết nối tới SQL Server
server = 'localhost,1434'
username = 'sa'
password = '1234QWER@'

# Kết nối đến database master để tạo database mới
connection = pyodbc.connect(f'DRIVER={{SQL Server}};SERVER={server};DATABASE=master;UID={username};PWD={password}')
cursor = connection.cursor()

# Tạo database nếu chưa tồn tại
try:
    cursor.execute("IF NOT EXISTS (SELECT * FROM sys.databases WHERE name = 'COData') "
                   "BEGIN "
                   "CREATE DATABASE COData; "
                   "END")
    connection.commit()  # Commit lệnh CREATE DATABASE
except Exception as e:
    print("Lỗi khi tạo cơ sở dữ liệu:", e)

# Đóng kết nối và mở lại kết nối tới database mới
connection.close()

# Kết nối đến database mới
connection = pyodbc.connect(f'DRIVER={{SQL Server}};SERVER={server};DATABASE=COData;UID={username};PWD={password}')
cursor = connection.cursor()

# Tạo bảng C/O
cursor.execute("""
    IF NOT EXISTS (SELECT * FROM sys.tables WHERE name = 'CO')
    BEGIN
        CREATE TABLE CO (
            doc_id NVARCHAR(50),
            Trạng_thái_hồ_sơ NVARCHAR(MAX),
            Tax_code NVARCHAR(50),
            Issuing_Authority NVARCHAR(100),
            Form NVARCHAR(50),
            Importing_Country NVARCHAR(100),
            Reference_No NVARCHAR(100),
            Issuance_date DATE,
            Certified_date DATE,
            total_value NVARCHAR(50),
            total_quantity NVARCHAR(50),
            total_weight NVARCHAR(50),
            declaration_place NVARCHAR(100)
        );
    END
""")
#tạo bảng transport
cursor.execute("""

    IF NOT EXISTS (SELECT * FROM sys.tables WHERE name = 'Transport')
    BEGIN
        CREATE TABLE Transport (
            doc_id NVARCHAR(50),
            transport_type NVARCHAR(50),
            departure_date DATE,
            vessel_aircraft_name NVARCHAR(100),
            port_of_loading NVARCHAR(100),
            port_of_discharge NVARCHAR(100),
            transport_doc NVARCHAR(MAX)
        );
    END               
               
""")
#tạo bảng from_to
cursor.execute("""
    IF NOT EXISTS (SELECT * FROM sys.tables WHERE name = 'from_to')
    BEGIN
        CREATE TABLE from_to (
            doc_id NVARCHAR(50),
            name_export NVARCHAR(100),
            address_export NVARCHAR(200),
            address_export2 NVARCHAR(200),
            name_import NVARCHAR(100),
            address_import NVARCHAR(200),
            address_import2 NVARCHAR(200)
        );
    END
""")

# Tạo bảng ExportDeclaration
cursor.execute("""
    IF NOT EXISTS (SELECT * FROM sys.tables WHERE name = 'ExportDeclaration')
    BEGIN
        CREATE TABLE ExportDeclaration (
            doc_id NVARCHAR(50),
            item_num INT,
            invoice_number NVARCHAR(50),
            invoice_date DATE,
            invoice_link NVARCHAR(MAX)
        );
    END
""")

# Tạo bảng Goods_info
cursor.execute("""
    IF NOT EXISTS (SELECT * FROM sys.tables WHERE name = 'Goods_info')
    BEGIN
        CREATE TABLE Goods_info (
            doc_id NVARCHAR(50),
            item_num INT,
            item_number INT,
            Id NVARCHAR(50),
            Marks_and_numbers_on_packages NVARCHAR(100),
            Goods_description NVARCHAR(200),
            Origin_criterion NVARCHAR(50),
            FOB_value NVARCHAR(100),
            Invoice_number_and_date NVARCHAR(100)
        );
    END
""")

# Tạo bảng Remarks_info
cursor.execute("""
    IF NOT EXISTS (SELECT * FROM sys.tables WHERE name = 'Remarks_info')
    BEGIN
        CREATE TABLE Remarks_info (
            doc_id NVARCHAR(50),
            label NVARCHAR(100),
            checked BIT
        );
    END
""")

connection.commit()  # Commit các lệnh tạo bảng

# Đóng kết nối
cursor.close()
connection.close()

print("Cơ sở dữ liệu và các bảng đã được tạo thành công.")


Cơ sở dữ liệu và các bảng đã được tạo thành công.


In [19]:
def convert_to_date(date_str):
    try:
        if date_str:
            return datetime.strptime(date_str.strip(), '%d/%m/%Y').date()  # Dùng định dạng dd/mm/yyyy
        return None  # Trả về None nếu không có ngày
    except ValueError:
        return None  # Trả về None nếu không thể chuyển đổi

In [17]:

def split_address(address_list):
    name = address_list[0].strip() if address_list else ''
    address1 = address_list[1].strip() if len(address_list) > 1 else ''
    address2 = address_list[2].strip() if len(address_list) > 2 else ''
    return name, address1, address2

In [25]:
# Kết nối đến SQL Server
connection = pyodbc.connect(f'DRIVER={{SQL Server}};SERVER={server};DATABASE=COData;UID={username};PWD={password}')
cursor = connection.cursor()

# Dữ liệu từ dict
data = all_id_info

# Chèn dữ liệu vào bảng CO
for record in data:
    # Lấy 'Issuance date' và 'Certified date' nếu tồn tại, nếu không có thì gán giá trị None
    issuance_date = convert_to_date(record.get('Issuance date', None))
    certified_date = convert_to_date(record.get('Certified date', None))
    
    cursor.execute("""
        INSERT INTO CO (doc_id, Trạng_thái_hồ_sơ, Tax_code, Issuing_Authority, Form, Importing_Country, Reference_No, Issuance_date, Certified_date, total_value, total_quantity, total_weight, declaration_place)
        VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
    """, record['doc_id'], record['Trạng thái hồ sơ'], record['Tax code'], record['Issuing Authority'], record['Form'],
        record['Importing_Country'], record['Reference No.'], issuance_date, certified_date, record['total_value'],
        record['total_quantity'], record['total_weight'], record['declaration_place'])

    # Chèn dữ liệu vào bảng Transport
    transport_type = record.get('transport_type', '')
    departure_date = convert_to_date(record.get('Departure Date', None))  # Kiểm tra ngày khởi hành
    vessel_aircraft_name = record.get('vessel_aircraft_name', '')
    port_of_loading = record.get('port_of_loading', '')
    port_of_discharge = record.get('port_of_discharge', '')
    transport_doc = record.get('transport_doc', '')

    cursor.execute("""
        INSERT INTO Transport (doc_id, transport_type, departure_date, vessel_aircraft_name, port_of_loading, port_of_discharge, transport_doc)
        VALUES (?, ?, ?, ?, ?, ?, ?)
    """, record['doc_id'], transport_type, departure_date, vessel_aircraft_name, port_of_loading, port_of_discharge, transport_doc)

    # Chèn dữ liệu vào bảng ExportDeclaration
    for export in record['ExportDeclaration']:
        export_invoice_date = convert_to_date(export.get('invoice_date', None))  # Kiểm tra ngày hóa đơn
        cursor.execute("""
            INSERT INTO ExportDeclaration (doc_id, item_num, invoice_number, invoice_date, invoice_link)
            VALUES (?, ?, ?, ?, ?)
        """, record['doc_id'], export['item_num'], export['invoice_number'], export_invoice_date, export['invoice_link'])

    # Chèn dữ liệu vào bảng Goods_info
    for idx, goods in enumerate(record['goods_info'][1:], 1):  # Bỏ qua dòng tiêu đề
        cursor.execute("""
            INSERT INTO Goods_info (doc_id, item_num, item_number, Id, Marks_and_numbers_on_packages, Goods_description, Origin_criterion, FOB_value, Invoice_number_and_date)
            VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?)
        """, record['doc_id'], idx, goods[0], goods[1], goods[2], goods[3], goods[4], goods[5], goods[6])

    # Chèn dữ liệu vào bảng Remarks_info, nếu tồn tại
    remarks_info = record.get('remarks_info', [])  # Nếu không có 'remarks_info', gán giá trị mặc định là list rỗng
    for remark in remarks_info:
        cursor.execute("""
            INSERT INTO Remarks_info (doc_id, label, checked)
            VALUES (?, ?, ?)
        """, record['doc_id'], remark['label'], remark['checked'])

    # Chèn dữ liệu vào bảng from_to
    def split_address(address_list):
        name = address_list[0].strip() if address_list else ''
        address1 = address_list[1].strip() if len(address_list) > 1 else ''
        address2 = address_list[2].strip() if len(address_list) > 2 else ''
        return name, address1, address2

    # Tách dữ liệu và chèn vào bảng
    name_export, address_export, address_export2 = split_address(record['Goods consigned from'])
    name_import, address_import, address_import2 = split_address(record['Goods consigned to'])

    # Chèn dữ liệu vào bảng from_to
    cursor.execute("""
        INSERT INTO from_to (doc_id, name_export, address_export, address_export2, name_import, address_import, address_import2)
        VALUES (?, ?, ?, ?, ?, ?, ?)
    """, record['doc_id'], name_export, address_export, address_export2, name_import, address_import, address_import2)

# Commit các thay đổi vào cơ sở dữ liệu
connection.commit()

# Đóng kết nối
cursor.close()
connection.close()

print("Dữ liệu đã được chèn thành công.")


Error: ('HYC00', '[HYC00] [Microsoft][ODBC SQL Server Driver]Optional feature not implemented (0) (SQLBindParameter)')